In [1]:
from pycocotools.coco import COCO
import json

import detectron2
from detectron2.engine import DefaultPredictor
from detectron2.config import get_cfg
from detectron2 import model_zoo

import cv2
import os
import numpy as np
import matplotlib.pyplot as plt
from detectron2.utils.visualizer import Visualizer
from detectron2.data import MetadataCatalog
import random

import tqdm
import multiprocessing
import pandas as pd

In [2]:
# Đường dẫn đến tập tin annotation COCO
coco_annotation_path = "E:/Download/annotations/instances_val2017.json"
coco = COCO(coco_annotation_path)

loading annotations into memory...
Done (t=2.50s)
creating index...
index created!


In [3]:
# Lấy các categories (danh mục đối tượng)
categories = coco.loadCats(coco.getCatIds())
category_names = [cat['name'] for cat in categories]

# In ra danh sách category_names
print(category_names)

['person', 'bicycle', 'car', 'motorcycle', 'airplane', 'bus', 'train', 'truck', 'boat', 'traffic light', 'fire hydrant', 'stop sign', 'parking meter', 'bench', 'bird', 'cat', 'dog', 'horse', 'sheep', 'cow', 'elephant', 'bear', 'zebra', 'giraffe', 'backpack', 'umbrella', 'handbag', 'tie', 'suitcase', 'frisbee', 'skis', 'snowboard', 'sports ball', 'kite', 'baseball bat', 'baseball glove', 'skateboard', 'surfboard', 'tennis racket', 'bottle', 'wine glass', 'cup', 'fork', 'knife', 'spoon', 'bowl', 'banana', 'apple', 'sandwich', 'orange', 'broccoli', 'carrot', 'hot dog', 'pizza', 'donut', 'cake', 'chair', 'couch', 'potted plant', 'bed', 'dining table', 'toilet', 'tv', 'laptop', 'mouse', 'remote', 'keyboard', 'cell phone', 'microwave', 'oven', 'toaster', 'sink', 'refrigerator', 'book', 'clock', 'vase', 'scissors', 'teddy bear', 'hair drier', 'toothbrush']


In [4]:
# Lấy các annotations
image_ids = coco.getImgIds()
annotations = coco.loadAnns(coco.getAnnIds(imgIds=image_ids))

# In một ví dụ về annotations
print(annotations[0])

{'segmentation': [[224.24, 297.18, 228.29, 297.18, 234.91, 298.29, 243.0, 297.55, 249.25, 296.45, 252.19, 294.98, 256.61, 292.4, 254.4, 264.08, 251.83, 262.61, 241.53, 260.04, 235.27, 259.67, 230.49, 259.67, 233.44, 255.25, 237.48, 250.47, 237.85, 243.85, 237.11, 240.54, 234.17, 242.01, 228.65, 249.37, 224.24, 255.62, 220.93, 262.61, 218.36, 267.39, 217.62, 268.5, 218.72, 295.71, 225.34, 297.55]], 'area': 1481.3806499999994, 'iscrowd': 0, 'image_id': 397133, 'bbox': [217.62, 240.54, 38.99, 57.75], 'category_id': 44, 'id': 82445}


In [5]:
# Cấu hình cho Predictors của Detectron2
cfg = get_cfg()
cfg.merge_from_file(model_zoo.get_config_file("COCO-Detection/faster_rcnn_R_50_FPN_3x.yaml"))
cfg.MODEL.WEIGHTS = model_zoo.get_checkpoint_url("COCO-Detection/faster_rcnn_R_50_FPN_3x.yaml")
cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = 0.7  # Ngưỡng để lọc các đối tượng
cfg.MODEL.DEVICE = "cpu"  # Sử dụng CPU thay vì GPU

predictor = DefaultPredictor(cfg)

In [6]:
# Thư mục chứa ảnh
image_folder = "E:/Download/val2017/"

# Lấy danh sách tất cả ảnh trong thư mục
image_files = [os.path.join(image_folder, f) for f in os.listdir(image_folder) if f.endswith(".jpg")]

# Chọn ngẫu nhiên 100 ảnh
num_display = 100
if len(image_files) > num_display:
    image_files = random.sample(image_files, num_display)  # Chọn 100 ảnh ngẫu nhiên

# Tạo Figure với lưới 10x10
fig, axes = plt.subplots(10, 10, figsize=(15, 15))

# Duyệt qua từng ảnh và hiển thị
for idx, image_path in enumerate(image_files):
    row = idx // 10  # Dòng hiện tại
    col = idx % 10   # Cột hiện tại

    image = cv2.imread(image_path)
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)  # Chuyển BGR thành RGB để hiển thị đúng màu

    axes[row, col].imshow(image)
    axes[row, col].axis("off")  # Ẩn trục tọa độ

# Hiển thị toàn bộ lưới ảnh
plt.tight_layout()
plt.show()

In [11]:
# Thư mục chứa ảnh
image_folder = "E:/Download/val2017/"

# Lấy danh sách tất cả ảnh trong thư mục
image_files = [os.path.join(image_folder, f) for f in os.listdir(image_folder) if f.endswith(".jpg")]

# Dictionary lưu kết quả
detected_objects = {}

# Dùng tqdm để hiển thị tiến trình
for image_path in tqdm.tqdm(image_files, desc="Processing images"):
    image = cv2.imread(image_path)
    outputs = predictor(image)  # Nhận diện đối tượng trên ảnh

    # Nếu có đối tượng được nhận diện, lưu lại thông tin
    if len(outputs["instances"].pred_classes) > 0:
        detected_objects[image_path] = []  # Danh sách đối tượng trong từng ảnh

        for i in range(len(outputs["instances"].pred_classes)):
            obj_class = outputs["instances"].pred_classes[i].item()
            confidence = outputs["instances"].scores[i].item()
            bbox = outputs["instances"].pred_boxes.tensor[i].tolist()

            # Lưu kết quả vào dictionary
            detected_objects[image_path].append({
                "object_class": obj_class,
                "confidence": confidence,
                "x1": bbox[0],
                "y1": bbox[1],
                "x2": bbox[2],
                "y2": bbox[3]
            })

Processing images: 100%|█████████████████████████████████████████████████████████| 5000/5000 [5:29:06<00:00,  3.95s/it]


In [13]:
# Chuyển kết quả nhận diện vào DataFrame để lưu lại
df_objects = []
for image_path, objects in detected_objects.items():
    for obj in objects:
        df_objects.append({
            "image_path": image_path,
            **obj  # Gộp thông tin object_class, confidence, x1, y1, x2, y2 vào
        })

df_objects = pd.DataFrame(df_objects)

# Lưu kết quả ra file CSV để xem
df_objects.to_csv("detected_objects.csv", index=False)

print("Saved detected_objects.csv")

Saved detected_objects.csv


In [15]:
# Lọc bỏ các đối tượng có object_class = 0
df_objects = df_objects[df_objects["object_class"] != 0]

# Lưu kết quả đã lọc ra file CSV
df_objects.to_csv("detected_objects_filtered.csv", index=False)

print("Saved detected_objects_filtered.csv")

Saved detected_objects_filtered.csv


In [14]:
# Tạo ánh xạ từ class ID sang tên thật của object trong COCO
category_dict = {cat['id']: cat['name'] for cat in categories}

# Chọn ngẫu nhiên 10 ảnh đã nhận diện để hiển thị với Visualizer
random_detected_images = random.sample(list(detected_objects.keys()), 10)

# Tạo thư mục để lưu ảnh nếu chưa tồn tại
output_folder = "output_images"
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

# Hiển thị ảnh với bounding box bằng Visualizer và lưu ảnh
fig, axes = plt.subplots(2, 5, figsize=(20, 10))

for idx, image_path in enumerate(random_detected_images):
    image = cv2.imread(image_path)
    
    # Chuyển BGR sang RGB để hiển thị đúng màu sắc
    image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

    # Thực hiện nhận diện lại để lấy dữ liệu bounding box
    outputs = predictor(image)

    # Tạo đối tượng Visualizer để vẽ bounding boxes lên ảnh
    v = Visualizer(image_rgb, MetadataCatalog.get(cfg.DATASETS.TRAIN[0]), scale=1.2)
    v = v.draw_instance_predictions(outputs["instances"].to("cpu"))
    
    # Lấy ảnh đã vẽ
    result_image = v.get_image()[:, :, ::-1]

    # Lưu ảnh đã vẽ vào thư mục output
    output_image_path = os.path.join(output_folder, f"image_{idx+1}.jpg")
    cv2.imwrite(output_image_path, result_image)

    # Hiển thị ảnh trong lưới 2x5
    row, col = idx // 5, idx % 5
    axes[row, col].imshow(result_image)
    axes[row, col].axis("off")
    axes[row, col].set_title(f"Image {idx+1}")

plt.tight_layout()
plt.show()

print(f"Đã lưu ảnh vào thư mục '{output_folder}'")

Đã lưu ảnh vào thư mục 'output_images'
